In [1]:
import json
import pandas as pd
pd.set_option('display.max_colwidth',100)
import numpy as np
from sklearn.model_selection import train_test_split
import tensorflow.keras as keras
import matplotlib.pyplot as plt
import math
import librosa, librosa.display

In [2]:
#training Data
metadata_train = pd.read_csv("E:/Project/vox1/metadata_train.txt", sep = ' ', header = None)
metadata_train.columns = ['true/false','location1','location2']
# metadata_train= pd.DataFrame(metadata_train)
y=metadata_train['location1'].unique()
y = pd.DataFrame(y)
y

0
0       id10001/Y8hIVOBuels/00001.wav
1       id10001/Y8hIVOBuels/00002.wav
2       id10001/Y8hIVOBuels/00003.wav
3       id10001/Y8hIVOBuels/00004.wav
4       id10001/Y8hIVOBuels/00005.wav
...                               ...
137919  id11251/5-6lI5JQtb8/00001.wav
137920  id11251/5-6lI5JQtb8/00002.wav
137921  id11251/5-6lI5JQtb8/00003.wav
137922  id11251/5-6lI5JQtb8/00004.wav
137923  id11251/5-6lI5JQtb8/00005.wav

[137924 rows x 1 columns]

In [3]:
y.columns=['location1']

In [4]:
output=[]

def reemovNestings(l):
    for i in l:
        if type(i) == list:
            reemovNestings(i)
        else:
            output.append(i)

In [5]:
data01=pd.DataFrame(columns=['labels','value'])
data01

Empty DataFrame
Columns: [labels, value]
Index: []

In [6]:
for i in y.index[:5000]:
    sample = y.loc[i,'location1']
    sample_1_path = 'E:/Project/vox1/wav/'+sample
    file = sample_1_path
#     print(file[31:38])
    signal, sample_rate = librosa.load(file, sr=16000)
#     data["labels"].append(sample[0:7]) 
#     data["value"].append(signal.tolist())
#     signal=""
    data1=pd.DataFrame([[sample[0:7],signal]],columns=['labels','value'])
#     print(data1)
    del signal
    data01=data01.append(data1)
    del data1
    print(i)
#     print(signal)
new=data01.groupby('labels').agg(lambda x: x.tolist())

# del data01

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [7]:
def removeNestings(k):
    List=[]
    for i in k: #i will be an array
        List.extend(i.tolist())
    List=np.asarray(List)
    return List

In [8]:
newmfcc=[]
for i in new.index:
    l=removeNestings(new['value'][i])
    MFCCs = librosa.feature.mfcc(l, 16000, n_fft=2048, hop_length=512, n_mfcc=13)
    mfcc=MFCCs.T
    shape = mfcc.shape[0]
    z=shape%200
    m=200-z
    n=shape+m
    mfcc1=np.resize(mfcc,(n,13))
    mfcc2=np.reshape(mfcc1,(int(n/200),200,13))
    newmfcc.append(mfcc2)

C:\Users\DELL\AppData\Local\Temp/ipykernel_14128/1073126786.py:4: FutureWarning: Pass y=[-0.05557251 -0.08816528 -0.10595703 ... -0.00033569 -0.00317383
 -0.00680542], sr=16000 as keyword args. From version 0.10 passing these as positional arguments will result in an error
  MFCCs = librosa.feature.mfcc(l, 16000, n_fft=2048, hop_length=512, n_mfcc=13)
C:\Users\DELL\AppData\Local\Temp/ipykernel_14128/1073126786.py:4: FutureWarning: Pass y=[ 0.01831055  0.02099609  0.02328491 ... -0.03533936 -0.03631592
 -0.02804565], sr=16000 as keyword args. From version 0.10 passing these as positional arguments will result in an error
  MFCCs = librosa.feature.mfcc(l, 16000, n_fft=2048, hop_length=512, n_mfcc=13)
C:\Users\DELL\AppData\Local\Temp/ipykernel_14128/1073126786.py:4: FutureWarning: Pass y=[-0.03527832  0.06304932  0.10134888 ... -0.01544189 -0.02062988
 -0.02416992], sr=16000 as keyword args. From version 0.10 passing these as positional arguments will result in an error
  MFCCs = librosa.

In [9]:
len(newmfcc)

43

In [10]:
newmel=[]
for i in new.index:
    lis=removeNestings(new['value'][i])  
    MEL = librosa.feature.melspectrogram(lis, 16000, n_fft=2048, hop_length=512, n_mels=13) 
    mel_spec=MEL.T 
    mel_shape = mel_spec.shape[0]
    mel_z=mel_shape%200
    mel=200-mel_z
    n=mel_shape+mel
    spec1=np.resize(mel_spec,(n,13))
    spec2=np.reshape(spec1,(int(n/200),200,13))
    newmel.append(spec2)

C:\Users\DELL\AppData\Local\Temp/ipykernel_14128/503219994.py:4: FutureWarning: Pass y=[-0.05557251 -0.08816528 -0.10595703 ... -0.00033569 -0.00317383
 -0.00680542], sr=16000 as keyword args. From version 0.10 passing these as positional arguments will result in an error
  MEL = librosa.feature.melspectrogram(lis, 16000, n_fft=2048, hop_length=512, n_mels=13)
C:\Users\DELL\AppData\Local\Temp/ipykernel_14128/503219994.py:4: FutureWarning: Pass y=[ 0.01831055  0.02099609  0.02328491 ... -0.03533936 -0.03631592
 -0.02804565], sr=16000 as keyword args. From version 0.10 passing these as positional arguments will result in an error
  MEL = librosa.feature.melspectrogram(lis, 16000, n_fft=2048, hop_length=512, n_mels=13)
C:\Users\DELL\AppData\Local\Temp/ipykernel_14128/503219994.py:4: FutureWarning: Pass y=[-0.03527832  0.06304932  0.10134888 ... -0.01544189 -0.02062988
 -0.02416992], sr=16000 as keyword args. From version 0.10 passing these as positional arguments will result in an error
 

In [11]:
len(newmel)

43

In [12]:
new

value
labels                                                                                                      
id10001  [[-0.05557251, -0.08816528, -0.10595703, -0.109558105, -0.1088562, -0.10195923, -0.084106445, -0...
id10002  [[0.018310547, 0.020996094, 0.023284912, 0.024627686, 0.025512695, 0.026153564, 0.025817871, 0.0...
id10003  [[-0.03527832, 0.06304932, 0.10134888, 0.08404541, 0.03237915, 0.13522339, 0.048431396, 0.061614...
id10004  [[0.01550293, 0.011108398, 0.0025939941, -0.014373779, -0.031280518, -0.041931152, -0.046051025,...
id10005  [[-0.0033569336, 0.0013427734, 0.004211426, 0.019073486, 0.042755127, 0.06777954, 0.080078125, 0...
id10006  [[-0.0043029785, 0.007873535, 0.01473999, 0.018310547, 0.022216797, 0.022125244, 0.021606445, 0....
id10007  [[0.0043945312, -0.0037231445, -0.00036621094, 0.0025939941, 0.008422852, -0.0012817383, 0.00308...
id10008  [[0.076934814, 0.041381836, -0.008514404, -0.047668457, -0.06765747, -0.06161499, -0.022460938, ...
id10009  [[-0.0017089844, -0.0023498535, -0.0010986328, 0.0030212402, 0.002166748, -0.0013122559, -0.0032...
id10010  [[-0.0008544922, -0.0012207031, -0.0012207031, -0.0010986328, -0.0012817383, -0.0011291504, -0.0...
id10011  [[0.096343994, 0.1331482, 0.15588379, 0.17086792, 0.19039917, 0.20770264, 0.22064209, 0.21835327...
id10012  [[-0.010284424, -0.011657715, -0.018341064, -0.02319336, -0.020874023, -0.0178833, -0.016784668,...
id10013  [[0.004638672, 0.00592041, 0.0093688965, 0.000579834, -0.011566162, -0.02053833, -0.028839111, -...
id10014  [[0.004180908, 0.00033569336, 0.012023926, 0.0050964355, -0.009429932, -0.0023498535, 0.00308227...
id10015  [[0.014862061, -0.006225586, -0.053649902, -0.1026001, -0.0579834, 0.0708313, 0.14526367, 0.0982...
id10016  [[0.27246094, 0.27877808, 0.34335327, 0.43014526, 0.44906616, 0.42980957, 0.39242554, 0.3515625,...
id10017  [[0.012207031, 0.014282227, 0.016784668, 0.019378662, 0.019714355, 0.017364502, 0.014862061, 0.0...
id10018  [[0.056884766, 0.06121826, 0.06958008, 0.07803345, 0.0819397, 0.08093262, 0.08074951, 0.07781982...
id10019  [[0.026611328, 0.011260986, -0.024383545, -0.024230957, -0.00592041, 0.017944336, 0.0015563965, ...
id10020  [[0.0010986328, 0.0015258789, 0.0010070801, 0.0009765625, 0.0005493164, -0.00015258789, 0.000122...
id10021  [[0.010498047, 0.009246826, 0.010040283, 0.009796143, 0.008911133, 0.0074768066, 0.0067443848, 0...
id10022  [[-0.018096924, -0.033203125, -0.047790527, -0.05722046, -0.065704346, -0.0690918, -0.062316895,...
id10023  [[0.031097412, 0.031402588, 0.033050537, 0.033935547, 0.028045654, 0.026123047, 0.023406982, 0.0...
id10024  [[-0.0079956055, -0.0064697266, -0.0049743652, -0.005004883, -0.0048217773, -0.0043945312, -0.00...
id10025  [[-0.08554077, -0.13043213, -0.17254639, -0.19995117, -0.20135498, -0.20172119, -0.17593384, -0....
id10026  [[-0.0022888184, -0.00036621094, -0.0012512207, -0.00045776367, 0.0014953613, 0.0038452148, 0.00...
id10027  [[-0.0019836426, 0.0049438477, -0.006591797, -0.012634277, -0.0066223145, -0.0026855469, -0.0003...
id10028  [[0.001373291, 0.0015258789, 0.0016174316, 0.0012817383, 0.0006713867, 0.00024414062, 0.00027465...
id10029  [[-9.1552734e-05, 0.0, -3.0517578e-05, -9.1552734e-05, -3.0517578e-05, 0.00021362305, 0.00024414...
id10030  [[-0.10873413, -0.14840698, -0.19195557, -0.22070312, -0.22451782, -0.21942139, -0.17971802, -0....
id10032  [[0.012084961, 0.054260254, 0.103393555, 0.14093018, 0.1479187, 0.12991333, 0.10003662, 0.059295...
id10033  [[-0.02130127, -0.0095825195, -0.017364502, -0.023895264, -0.007965088, -0.006713867, -0.0154418...
id10034  [[0.00033569336, -0.0004272461, -0.00045776367, -0.00091552734, -0.0017700195, -0.0017089844, -0...
id10035  [[-0.10055542, -0.0491333, -0.036346436, -0.056396484, -0.08856201, -0.103302, -0.10058594, -0.0...
id10036  [[0.017608643, 0.012908936, 0.017486572, 0.023132324, 0.017150879, 0.011474609, 0.010620117, 0.0...
id10038  [[-0.0074768066, -0.0028381348, -0.0031433105, -0.004547119, 

In [13]:
  #making 2d arrays from 3d array
currentarr=[]
for i in range(0,len(new.index)):
    split=np.array_split(newmfcc[i],len(newmfcc[i]))
    print(len(newmfcc[i]))
    split=np.asarray(split)
    for j in range(0,len(split)):
        z=np.reshape(split[j],(200,13))
        print(z)
        currentarr.append(z)
currentarr=np.asarray(currentarr)

91
[[-177.80406143  141.10105188  -50.59793166 ...    3.0567477
   -10.27750628  -21.47763152]
 [-172.48179279  125.0318206   -60.77817706 ...   -3.17132013
    -5.99933576  -22.62035693]
 [-188.12133225  104.9453401   -62.67864517 ...   -6.31022779
    -5.53904717  -26.14233564]
 ...
 [-279.4619747    55.31853471   55.1983806  ...   -8.02965581
   -10.50057694   -7.77481674]
 [-305.18695346   15.62198483   81.5258402  ...   -8.27146807
    -7.60830841  -11.36165327]
 [-306.7886776    13.31199117   74.25481708 ...  -14.01179007
    -5.72194474   -3.73421612]]
[[-291.50428172   65.08526058   57.56197675 ...  -23.54851217
    -9.05489271    7.01497336]
 [-286.21986504   95.74549202   23.62797726 ...  -20.87291074
    -7.63854938    5.55683833]
 [-291.31482181  100.3182379     6.18354314 ...  -12.54532762
    -5.65277432   -7.66783366]
 ...
 [-338.42539979   18.33747275    9.98578221 ...   -9.58631471
    -9.03907311    4.35680044]
 [-351.63372778   32.92435209    4.06846027 ...   -6.5002

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [14]:
#making 2d arrays from 3d array
currarr=[]
for i in range(0, len(new.index)):
    arr_split=np.array_split(newmel[i], len(newmel[i]))
    print(len(newmel[i]))
    arr_split=np.asarray(arr_split)
    for j in range(0, len(arr_split)):
        mel_z=np.reshape(arr_split[j],(200,13))
        print(mel_z)
        currarr.append(mel_z)
currarr=np.asarray(currarr)

91
[[3.78222003e-01 6.48598600e-01 1.74511358e+01 ... 3.14038400e-03
  2.69093793e-04 3.21750717e-04]
 [6.37462350e-01 8.31558272e-01 2.97119624e+01 ... 6.07341648e-03
  5.55712256e-04 6.01007314e-04]
 [6.21692918e-01 7.47011635e-01 2.90721392e+01 ... 9.17737668e-03
  7.43559532e-04 7.47915989e-04]
 ...
 [1.46209437e+00 2.66471931e-01 2.71926919e-02 ... 1.82047897e-03
  6.47184333e-03 2.11048215e-03]
 [4.72575098e-01 6.58110208e-02 3.18597232e-03 ... 5.23164632e-03
  3.33681880e-02 8.93098275e-03]
 [2.11510165e-01 4.07488246e-02 3.39378714e-03 ... 3.18851148e-03
  3.00617166e-02 1.27678207e-02]]
[[5.12276212e-01 4.03346769e-01 6.12807891e-02 ... 5.22085102e-04
  5.94840728e-03 3.93780483e-03]
 [1.07372090e+00 1.31580233e+00 1.96784011e-01 ... 3.37915773e-04
  5.40083291e-04 4.49264551e-04]
 [1.06873053e+00 1.49688580e+00 1.84859441e-01 ... 8.00291814e-04
  1.78992771e-04 1.37503543e-04]
 ...
 [9.34543035e-03 1.56087568e-03 5.95003440e-04 ... 9.01100610e-04
  1.20181308e-03 6.88870953e-

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [15]:
#print(currentarr.shape)
#print(currentarr[0])

In [16]:
len(newmfcc)

43

In [17]:
lbl=[]
i=0
for each in new.index:
    if(i<len(new.index)):
        #print(each)
        c=0
        while(c<len(newmfcc[i])):
            #print(len(newmfcc[i]))
            lbl.append(each)
            c=c+1
        i=i+1
    else:
        break

In [18]:
print(len(lbl))

6208


In [19]:
merged_list = pd.DataFrame(data=zip(lbl,currentarr), columns=['index', 'values'])

In [20]:
merged_list

index  \
0     id10001   
1     id10001   
2     id10001   
3     id10001   
4     id10001   
...       ...   
6203  id10045   
6204  id10045   
6205  id10045   
6206  id10045   
6207  id10045   

                                                                                                   values  
0     [[-177.80406143022944, 141.10105187529197, -50.59793166086991, -23.02146399151925, -34.047522577...  
1     [[-291.5042817154489, 65.0852605756359, 57.561976747986854, 1.2394840996226497, 28.9387573121378...  
2     [[-362.66742781978496, 69.03213822049656, -25.15697195298555, 42.018442995059715, 17.74120703642...  
3     [[-274.25247598808033, 86.22092757841777, 17.86873124276029, 73.44343830742915, 14.4658749010908...  
4     [[-175.8239409936965, -0.6739491781460334, 44.002591293117774, 46.871159534130335, -9.6998991463...  
...                                                                                                   ...  
6203  [[-174.02201005095517, 88.76174612211804, 24.676197886478505, 7.404524828561355, -0.474451395194...  
6204  [[-82.15547264841372, 117.60884680033593, 22.851892155979833, 0.4159076538571256, -35.0077817336...  
6205  [[-116.58698134719872, 102.8202661172954, 27.91145150148164, 28.699337773759595, 16.245499032822...  
6206  [[-71.22881819627594, 147.16063130157744, 12.047665823413784, -9.893032692052795, -6.19799607192...  
6207  [[-48.46247450830369, 108.55607545055823, -7.932282463950002, 29.045922807303427, 3.535068831731...  

[6208 rows x 2 columns]

In [21]:
import random
c1 = list(zip(currentarr, lbl))
random.shuffle(c1)
mfcc_val, mfcc_index = zip(*c1)

In [22]:
import random
c2 = list(zip(currarr, lbl))
random.shuffle(c2)
mel_val, mel_index = zip(*c2)

In [23]:
# print(values[5])
# print(index[5])

In [24]:
mfcc_val=np.asarray(mfcc_val)

In [25]:
mel_val=np.asarray(mel_val)

In [26]:
# print(lbl[91])
# print(currentarr[91:200])

In [28]:
#labels into array
import numpy as np
from keras.utils.np_utils import to_categorical
from sklearn import preprocessing
labelEncode=preprocessing.LabelEncoder()
labelEncode.fit(mfcc_index)
print (labelEncode.classes_)
train_labelEncode=labelEncode.transform(mfcc_index)
mfcc_label=to_categorical(np.asarray(train_labelEncode))
mfcc_label

['id10001' 'id10002' 'id10003' 'id10004' 'id10005' 'id10006' 'id10007'
 'id10008' 'id10009' 'id10010' 'id10011' 'id10012' 'id10013' 'id10014'
 'id10015' 'id10016' 'id10017' 'id10018' 'id10019' 'id10020' 'id10021'
 'id10022' 'id10023' 'id10024' 'id10025' 'id10026' 'id10027' 'id10028'
 'id10029' 'id10030' 'id10032' 'id10033' 'id10034' 'id10035' 'id10036'
 'id10038' 'id10039' 'id10040' 'id10041' 'id10042' 'id10043' 'id10044'
 'id10045']


array([[0., 1., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]], dtype=float32)

In [29]:
#labels into array
import numpy as np
from keras.utils.np_utils import to_categorical
from sklearn import preprocessing
labelEncode=preprocessing.LabelEncoder()
labelEncode.fit(mel_index)
print (labelEncode.classes_)
train_labelEncode=labelEncode.transform(mel_index)
mel_label=to_categorical(np.asarray(train_labelEncode))
mel_label

['id10001' 'id10002' 'id10003' 'id10004' 'id10005' 'id10006' 'id10007'
 'id10008' 'id10009' 'id10010' 'id10011' 'id10012' 'id10013' 'id10014'
 'id10015' 'id10016' 'id10017' 'id10018' 'id10019' 'id10020' 'id10021'
 'id10022' 'id10023' 'id10024' 'id10025' 'id10026' 'id10027' 'id10028'
 'id10029' 'id10030' 'id10032' 'id10033' 'id10034' 'id10035' 'id10036'
 'id10038' 'id10039' 'id10040' 'id10041' 'id10042' 'id10043' 'id10044'
 'id10045']


array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 1., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 1., 0., 0.]], dtype=float32)

In [31]:
#TRAIN TEST SPLIT FOR MFCC
X_train1, X_test1, y_train1, y_test1 = train_test_split(mfcc_val, mfcc_label, test_size=0.3)

In [32]:
#TRAIN TEST SPLIT FOR SPECTOGRAM
X_train2, X_test2, y_train2, y_test2 = train_test_split(mel_val, mel_label, test_size=0.3)

In [33]:
import tensorflow as tf
from keras.models import Sequential,Model
from keras.layers import Dense
from keras.layers import Flatten
from keras.layers.convolutional import Conv2D
from keras.layers.convolutional import MaxPooling2D
from tensorflow.keras.layers import Conv1D, GlobalMaxPooling1D, MaxPooling1D,LSTM,Bidirectional,GlobalAveragePooling1D,Dropout, Activation, Flatten, Embedding,Input

In [34]:
inputs = Input(shape=(200, 13))
conv = Conv1D(filters=32, kernel_size=2, activation='relu')(inputs)
pool = MaxPooling1D(pool_size=(5))(conv)
conv2=Conv1D(64,(3),activation='relu')(pool)
pool2=MaxPooling1D(pool_size=(2),padding='same')(conv2)
flat = Flatten()(pool2)

In [35]:
dense1 = Dense(128, activation='relu')(flat)
outputs = Dense(len(new.index), activation='sigmoid')(dense1)
model = Model(inputs=inputs, outputs=outputs)
model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 200, 13)]         0         
                                                                 
 conv1d (Conv1D)             (None, 199, 32)           864       
                                                                 
 max_pooling1d (MaxPooling1D  (None, 39, 32)           0         
 )                                                               
                                                                 
 conv1d_1 (Conv1D)           (None, 37, 64)            6208      
                                                                 
 max_pooling1d_1 (MaxPooling  (None, 19, 64)           0         
 1D)                                                             
                                                                 
 flatten (Flatten)           (None, 1216)              0     

In [36]:
tf.keras.utils.plot_model(model, to_file='model_test.png', show_shapes=True, show_layer_names=True)

You must install pydot (`pip install pydot`) and install graphviz (see instructions at https://graphviz.gitlab.io/download/) for plot_model/model_to_dot to work.


In [37]:
model.compile(loss = 'categorical_crossentropy', optimizer = 'Adam', metrics = ['accuracy'])

In [38]:
model.fit(X_train1,y_train1, validation_data=(X_test1,y_test1), epochs = 100, verbose = 1,shuffle=True)
# model.fit(currentarr,label,  epochs = 100, verbose = 1)

Epoch 1/100
136/136 [==============================] - 2s 8ms/step - loss: 8.3678 - accuracy: 0.0364 - val_loss: 3.7490 - val_accuracy: 0.0714
Epoch 2/100
136/136 [==============================] - 1s 7ms/step - loss: 3.7378 - accuracy: 0.0550 - val_loss: 3.7341 - val_accuracy: 0.0682
Epoch 3/100
136/136 [==============================] - 1s 7ms/step - loss: 3.7179 - accuracy: 0.0557 - val_loss: 3.7155 - val_accuracy: 0.0751
Epoch 4/100
136/136 [==============================] - 1s 7ms/step - loss: 3.7010 - accuracy: 0.0575 - val_loss: 3.7746 - val_accuracy: 0.0719
Epoch 5/100
136/136 [==============================] - 1s 6ms/step - loss: 3.6878 - accuracy: 0.0596 - val_loss: 3.6919 - val_accuracy: 0.0709
Epoch 6/100
136/136 [==============================] - 1s 7ms/step - loss: 3.6554 - accuracy: 0.0608 - val_loss: 3.6602 - val_accuracy: 0.0859
Epoch 7/100
136/136 [==============================] - 1s 6ms/step - loss: 3.6091 - accuracy: 0.0895 - val_loss: 3.6158 - val_accuracy: 0.0837

In [39]:
model.fit(X_train2,y_train2, validation_data=(X_test2,y_test2), epochs = 100, verbose = 1,shuffle=True)
# model.fit(currentarr,label,  epochs = 100, verbose = 1)

Epoch 1/100
136/136 [==============================] - 1s 7ms/step - loss: 4.5817 - accuracy: 0.0550 - val_loss: 3.5949 - val_accuracy: 0.0548
Epoch 2/100
136/136 [==============================] - 1s 7ms/step - loss: 3.5398 - accuracy: 0.0642 - val_loss: 3.5906 - val_accuracy: 0.0709
Epoch 3/100
136/136 [==============================] - 1s 7ms/step - loss: 3.4301 - accuracy: 0.0987 - val_loss: 3.4341 - val_accuracy: 0.1079
Epoch 4/100
136/136 [==============================] - 1s 7ms/step - loss: 3.3455 - accuracy: 0.1109 - val_loss: 3.3804 - val_accuracy: 0.1122
Epoch 5/100
136/136 [==============================] - 1s 7ms/step - loss: 3.2418 - accuracy: 0.1289 - val_loss: 3.2865 - val_accuracy: 0.1095
Epoch 6/100
136/136 [==============================] - 1s 7ms/step - loss: 3.1015 - accuracy: 0.1480 - val_loss: 3.2508 - val_accuracy: 0.1272
Epoch 7/100
136/136 [==============================] - 1s 7ms/step - loss: 2.9960 - accuracy: 0.1659 - val_loss: 3.1521 - val_accuracy: 0.1492

In [40]:
test_predictions_mfcc = model.predict(X_test1)
# Finding out of two output neurons which one has highest probability
# It will return us the predicted class
# It will convert probability into final class 1 and 0
test_predictions1 = np.zeros_like(test_predictions_mfcc)
test_predictions1[np.arange(len(test_predictions_mfcc)), test_predictions_mfcc.argmax(1)] = 1


59/59 [==============================] - 0s 2ms/step


In [41]:
test_predictions_mel = model.predict(X_test2)
# Finding out of two output neurons which one has highest probability
# It will return us the predicted class
# It will convert probability into final class 1 and 0
test_predictions2 = np.zeros_like(test_predictions_mel)
test_predictions2[np.arange(len(test_predictions_mel)), test_predictions_mel.argmax(1)] = 1


59/59 [==============================] - 0s 2ms/step


In [42]:
#Accuracy 
from sklearn.metrics import classification_report
print(classification_report(y_test1,test_predictions1))

              precision    recall  f1-score   support

           0       0.01      0.03      0.01        34
           1       0.08      0.03      0.05        31
           2       0.02      0.13      0.03        47
           3       0.05      0.09      0.06        43
           4       0.00      0.00      0.00        22
           5       0.05      0.38      0.08        52
           6       0.02      0.13      0.04        31
           7       0.00      0.00      0.00        50
           8       0.00      0.00      0.00        25
           9       0.01      0.16      0.03        19
          10       0.00      0.00      0.00        56
          11       0.08      0.12      0.10        50
          12       0.00      0.00      0.00        15
          13       0.01      0.03      0.01        36
          14       0.00      0.00      0.00        20
          15       0.10      0.04      0.06       134
          16       0.00      0.00      0.00        49
          17       0.00    

C:\Users\DELL\anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [43]:
#Accuracy 
from sklearn.metrics import classification_report
print(classification_report(y_test2,test_predictions2))

              precision    recall  f1-score   support

           0       0.15      0.22      0.18        23
           1       0.24      0.52      0.33        33
           2       0.17      0.20      0.18        51
           3       0.15      0.13      0.14        46
           4       0.11      0.12      0.12        24
           5       0.28      0.30      0.29        61
           6       0.23      0.23      0.23        39
           7       0.11      0.17      0.13        35
           8       0.00      0.00      0.00        18
           9       0.17      0.33      0.23        12
          10       0.14      0.10      0.12        49
          11       0.17      0.28      0.21        47
          12       0.07      0.05      0.05        22
          13       0.07      0.06      0.06        33
          14       0.12      0.08      0.10        25
          15       0.35      0.27      0.30       109
          16       0.07      0.09      0.08        33
          17       0.36    